## Modelling

## Import the required modules

In [1]:
from keras.models import Sequential
from keras.layers import Convolution2D
from keras.layers import MaxPooling2D
from keras.layers import Flatten , Dropout
from keras.layers import Dense
from keras.preprocessing.image import ImageDataGenerator

2023-07-14 16:02:22.423503: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.10.1


### 1- Preparing the train and test data

In [4]:
train_data = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True
)

test_data = ImageDataGenerator(rescale=1./255)

training_set = train_data.flow_from_directory(r'../Pre processing/Adaptive Threshold Mean Rename/Train/',
    target_size=(96, 96),
    batch_size=10,
    color_mode='grayscale',
    class_mode='categorical'
)

testing_set = test_data.flow_from_directory(r'../Pre processing/Adaptive Threshold Mean Rename/Test/',
    target_size=(96, 96),
    batch_size=10, #5
    color_mode='grayscale',
    class_mode='categorical'
) 

Found 32000 images belonging to 32 classes.
Found 22400 images belonging to 32 classes.


### 2- Build the CNN model

In [5]:
# Initializing the CNN or Neural Network
classifier = Sequential()

# First convolution layer and pooling
classifier.add(Convolution2D(32, (3, 3), input_shape=(96, 96, 1), activation='relu'))
classifier.add(MaxPooling2D(pool_size=(2, 2)))

# Avoiding 25% of the neurons to avoid overfitting of the data.
classifier.add(Dropout(0.25))

# Second convolution layer and pooling
classifier.add(Convolution2D(64, (3, 3), activation='relu'))
classifier.add(MaxPooling2D(pool_size=(2, 2)))

# Third convolution layer and pooling
classifier.add(Convolution2D(128, (3, 3), activation='relu'))
classifier.add(MaxPooling2D(pool_size=(2, 2)))

# Fourth convolution layer and pooling
classifier.add(Convolution2D(256, (3, 3), activation='relu'))
classifier.add(MaxPooling2D(pool_size=(2, 2)))

# Flattening the layers
classifier.add(Flatten())

# Connecting all layers together.
classifier.add(Dense(units=128, activation='relu'))
classifier.add(Dense(units=32, activation='softmax'))

# Compile the CNN model.
classifier.compile(
    optimizer='adam',
    loss='categorical_crossentropy',
    metrics=['accuracy']
)

classifier.fit(
        training_set,
        epochs=5,
        validation_data=testing_set
)

2023-07-14 16:07:18.086409: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:116] None of the MLIR optimization passes are enabled (registered 2)
2023-07-14 16:07:18.120671: I tensorflow/core/platform/profile_utils/cpu_utils.cc:112] CPU Frequency: 1696055000 Hz


Epoch 1/5
   1/3200 [..............................] - ETA: 1:58:25 - loss: 3.4904 - accuracy: 0.0000e+00

2023-07-14 16:07:20.412359: W tensorflow/core/framework/cpu_allocator_impl.cc:80] Allocation of 21196800 exceeds 10% of free system memory.
2023-07-14 16:07:20.452171: W tensorflow/core/framework/cpu_allocator_impl.cc:80] Allocation of 25660800 exceeds 10% of free system memory.


   2/3200 [..............................] - ETA: 12:40 - loss: 3.5293 - accuracy: 0.0000e+00  

2023-07-14 16:07:20.640592: W tensorflow/core/framework/cpu_allocator_impl.cc:80] Allocation of 21196800 exceeds 10% of free system memory.
2023-07-14 16:07:20.685648: W tensorflow/core/framework/cpu_allocator_impl.cc:80] Allocation of 25660800 exceeds 10% of free system memory.


   3/3200 [..............................] - ETA: 13:02 - loss: 3.5278 - accuracy: 0.0000e+00

2023-07-14 16:07:20.906729: W tensorflow/core/framework/cpu_allocator_impl.cc:80] Allocation of 21196800 exceeds 10% of free system memory.


3200/3200 [==============================] - 1013s 316ms/step - loss: 0.8834 - accuracy: 0.7508 - val_loss: 9.5539e-04 - val_accuracy: 0.9997
Epoch 2/5
3200/3200 [==============================] - 742s 232ms/step - loss: 0.0215 - accuracy: 0.9937 - val_loss: 6.4800e-04 - val_accuracy: 0.9997
Epoch 3/5
3200/3200 [==============================] - 725s 227ms/step - loss: 0.0107 - accuracy: 0.9971 - val_loss: 9.8344e-04 - val_accuracy: 0.9996
Epoch 4/5
3200/3200 [==============================] - 775s 242ms/step - loss: 0.0076 - accuracy: 0.9983 - val_loss: 1.3547e-04 - val_accuracy: 1.0000
Epoch 5/5
3200/3200 [==============================] - 803s 251ms/step - loss: 0.0128 - accuracy: 0.9977 - val_loss: 2.2006e-05 - val_accuracy: 1.0000


In [6]:
classifier.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_4 (Conv2D)            (None, 94, 94, 32)        320       
_________________________________________________________________
max_pooling2d_4 (MaxPooling2 (None, 47, 47, 32)        0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 47, 47, 32)        0         
_________________________________________________________________
conv2d_5 (Conv2D)            (None, 45, 45, 64)        18496     
_________________________________________________________________
max_pooling2d_5 (MaxPooling2 (None, 22, 22, 64)        0         
_________________________________________________________________
conv2d_6 (Conv2D)            (None, 20, 20, 128)       73856     
_________________________________________________________________
max_pooling2d_6 (MaxPooling2 (None, 10, 10, 128)      

### 3- Save the model

In [4]:
model_json = classifier.to_json()
with open("model_03.json", "w") as json_file:
    json_file.write(model_json)
classifier.save_weights('model_03.h5')

## Predicting

### Import Required Modules

In [6]:
from keras.models import model_from_json
import numpy as np
import cv2 as cv
import operator, random
import glob, sys, os

### 1- Loading the model

In [7]:
json_file = open("model_03.json", "r")
model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(model_json)

# load weights into new model
loaded_model.load_weights("model_03.h5")
print("Loaded model from disk")

Loaded model from disk


### 2- Test the prediction of model

In [8]:
font = cv.FONT_HERSHEY_COMPLEX_SMALL

capture = cv.VideoCapture(0)

while True:
    _, frame = capture.read()
    height,width = frame.shape[:2] # frame.shape[0] -> height, frame.shape[1] -> width
    
    # Simulating mirror image
    frame = cv.flip(frame, 1)
    
    # Got this from collect-data.py
    # Coordinates of the ROI(Region of interested)
    x1 = int(0.5*frame.shape[1])
    y1 = 10
    x2 = frame.shape[1]-10
    y2 = int(0.5*frame.shape[1])
    
    # Drawing the ROI for bounding box
    cv.rectangle(frame, (x1-1, y1-1), (x2+1, y2+1), (255,0,0) ,1)
    
    # Extracting the ROI
    roi = frame[y1:y2, x1:x2]

    # Resizing the ROI so it can be fed to the model for prediction
    roi = cv.resize(roi, (96, 96)) 
    roi = cv.cvtColor(roi, cv.COLOR_BGR2GRAY)
    blur_img = cv.medianBlur(roi, 5)
    test_image = cv.adaptiveThreshold(blur_img, 255, cv.ADAPTIVE_THRESH_MEAN_C, cv.THRESH_BINARY, 11, 2)
    cv.imshow("Result", test_image)
    
    # Batch of 1
    result = loaded_model.predict(test_image.reshape(1, 96, 96, 1))
    print(result)
    
    prediction = {
        'Alef' : result[0][0],
        'Alef A' : result[0][1],
        'Ayen' : result[0][2],
        'Beeh' : result[0][3],
        'Daal' : result[0][4],
        'Feeh' : result[0][5],
        'Gaph' : result[0][6],
        'Ghain' : result[0][7],
        'Heeh' : result[0][8],
        'Heeh 2' : result[0][9],
        'Hamza' : result[0][10],
        'Jeem' : result[0][11],
        'Kaph' : result[0][12],
        'Kheh' : result[0][13],
        'Laam' : result[0][14],
        'Meem' : result[0][15],
        'Nonn' : result[0][16],
        'Peeh' : result[0][17],
        'Qaph' : result[0][18],
        'Reeh' : result[0][19],
        'Seeh' : result[0][20],
        'Saad' : result[0][21],
        'Shen' : result[0][22],
        'Seen' : result[0][23],
        'Teeh' : result[0][24],
        'Toyy' : result[0][25],
        'Woww' : result[0][26],
        'Yaah' : result[0][27],
        'Zaal' : result[0][28],
        'Zaad' : result[0][29],
        'Zeeh' : result[0][30],
        'Zoyy' : result[0][31],
    }
    
    sa =max(result[0]*100)
    print("\n",sa,result[0])
    
    
    # Sorting based on top prediction
    prediction = sorted(prediction.items(), key=operator.itemgetter(1), reverse=True)
    
    # Displaying the predictions
    cv.rectangle(frame, (x1, y1+260) , (x2, y2) , (0,0,0),-6)

    if sa>99:
        # Displaying the predictions
        cv.putText(frame,"  " + prediction[0][0],(x1, y1+290), font, 1,(255,255,255),1,cv.LINE_AA)
        pred = prediction[0][0]
                    
    cv.putText(frame, prediction[0][0], (10, 120), cv.FONT_HERSHEY_PLAIN, 1, (145,195,215), 1)
    cv.imshow("Result", frame)
    
    interrupt = cv.waitKey(1)
    if interrupt & 0xFF == ord('q'): # Esc key
        break

capture.release()
cv.destroyAllWindows()

[ WARN:0@80.089] global /opt/conda/conda-bld/opencv-suite_1663872516975/work/modules/videoio/src/cap_gstreamer.cpp (862) isPipelinePlaying OpenCV | GStreamer warning: GStreamer: pipeline have not been created
libGL error: MESA-LOADER: failed to open crocus: /usr/lib/dri/crocus_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)
libGL error: failed to load driver: crocus
libGL error: MESA-LOADER: failed to open crocus: /usr/lib/dri/crocus_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)
libGL error: failed to load driver: crocus
libGL error: MESA-LOADER: failed to open swrast: /usr/lib/dri/swrast_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)
libGL error: failed to load driver: swr

[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 1. 0. 0. 0. 0. 0. 0.]]

 100.0 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.

[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.

[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.

[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]]

 100.0 [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0.]
[[1.1719253e-33 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  1.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
  0.0000000e+00 0.0000000e+00]]

 100.0 [1.1719253e-33 0.0000000e+00 0.0000000e+00 0.0000000e+00 0.0000000e+00
 0.0000000e+00 0.0000000e+00 0.0000000e

...

[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
  0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
  0.03363304 0.02911993]]

 3.982909 [0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
 0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
 0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
 0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
 0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
 0.03363304 0.02911993]
[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.0

[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
  0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
  0.03363304 0.02911993]]

 3.982909 [0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
 0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
 0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
 0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
 0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
 0.03363304 0.02911993]
[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.0

[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
  0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
  0.03363304 0.02911993]]

 3.982909 [0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
 0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
 0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
 0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
 0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
 0.03363304 0.02911993]
[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.0

[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
  0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
  0.03363304 0.02911993]]

 3.982909 [0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
 0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
 0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
 0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
 0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
 0.03363304 0.02911993]
[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.0

[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
  0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
  0.03363304 0.02911993]]

 3.982909 [0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
 0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
 0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
 0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.03237355
 0.03085586 0.0293175  0.03150631 0.03205098 0.0300819  0.02930968
 0.03363304 0.02911993]
[[0.03234759 0.03068451 0.03005864 0.03238538 0.03332742 0.03412464
  0.03166643 0.03091261 0.03982909 0.03152734 0.0295075  0.02825754
  0.03124109 0.02942484 0.03126924 0.03367277 0.03097385 0.03245787
  0.03287276 0.02992073 0.02913601 0.0276899  0.02846351 0.0